In [1]:
import numpy as np
import os
import sys
import pandas as pd
import seaborn as sns

import pylab as pl
import h5py

import tensorflow as tf
from tensorflow.keras import mixed_precision

os.environ['TF_CPP_MIN_LOG_LEVEL']='2'
os.environ['CUDA_VISIBLE_DEVICES']="0" 

gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
  try:
    # Currently, memory growth needs to be the same across GPUs
    for gpu in gpus:
      tf.config.experimental.set_memory_growth(gpu, True)
    logical_gpus = tf.config.experimental.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
  except RuntimeError as e:
    # Memory growth must be set before GPUs have been initialized
    print(e)


from sklearn.metrics import confusion_matrix

base_dir = '/media/tord/T7/Thesis_ssd/MasterThesis3'
os.chdir(base_dir)
from Classes.DataProcessing.LoadData import LoadData
from Classes.DataProcessing.HelperFunctions import HelperFunctions
from Classes.DataProcessing.DataHandler import DataHandler
from Classes.Modeling.DynamicModels import DynamicModels
from Classes.Modeling.TrainSingleModelRam import TrainSingleModelRam
from Classes.DataProcessing.RamLoader import RamLoader
import json

import gc

import datetime
import re
from livelossplot import PlotLossesKeras
from GlobalUtils import GlobalUtils
from Classes.Modeling.CustomCallback import CustomCallback
from tensorflow.keras.callbacks import EarlyStopping
utils = GlobalUtils()

from tensorflow.keras.utils import GeneratorEnqueuer






import sys


helper = HelperFunctions()

tf.config.optimizer.set_jit(True)
mixed_precision.set_global_policy('mixed_float16')

1 Physical GPUs, 1 Logical GPUs

INFO:tensorflow:Mixed precision compatibility check (mixed_float16): OK
Your GPU will likely run quickly with dtype policy mixed_float16 as it has compute capability of at least 7.0. Your GPU: GeForce RTX 3090, compute capability 8.6


In [2]:
load_args = {
    'earth_explo_only' : True,
    'noise_earth_only' : False,
    'noise_not_noise' : False,
    'downsample' : True,
    'upsample' : True,
    'frac_diff' : 1,
    'seed' : 1,
    'subsample_size' : 0.25,
    'balance_non_train_set' : False,
    'use_true_test_set' : False,
    'even_balance' : True
}
loadData = LoadData(**load_args)
train_ds, val_ds, test_ds = loadData.get_datasets()
noise_ds = loadData.noise_ds
handler = DataHandler(loadData)



2 2
Mapping train redundancy: : [--------------------------------------->] 100 %

Mapping validation redundancy: : [--------------------------------------->] 100 %

Mapping test redundancy: : [--------------------------------------->] 100 %



Loaded explosion and earthquake dataset:
Evenly balanced among classes in the train set.
Distribution (Label: (counts, proportion)) of
Train ds:
earthquake: (20507, 0.4987)  |  explosion: (20616, 0.5013)  
Val ds:
earthquake: (255, 0.0762)  |  explosion: (3092, 0.9238)  
Test ds:
earthquake: (176, 0.0789)  |  explosion: (2055, 0.9211)  


In [3]:
model_type = "CNN_grow_double"
is_lstm = True
num_channels = 3    

use_time_augmentor = True
scaler_name = "normalize"
use_noise_augmentor = True
filter_name = None
band_min = 2.0
band_max = 4.0
highpass_freq = 0.075


shutdown = False

num_classes = len(list(set(loadData.label_dict.values())))



ramLoader = RamLoader(loadData, 
                      handler, 
                      use_time_augmentor = use_time_augmentor, 
                      use_noise_augmentor = use_noise_augmentor, 
                      scaler_name = scaler_name,
                      filter_name = filter_name, 
                      band_min = band_min,
                      band_max = band_max,
                      highpass_freq = highpass_freq, 
                      load_test_set = True, 
                      meier_load = False)

x_train, y_train, x_val, y_val, x_test, y_test, noiseAug = ramLoader.load_to_ram()

Fitting noise set time augmentor: [--------------------------------------->] 100 %

Fit process completed after 10.309063911437988 seconds. Total datapoints fitted: 21199.
Average time per datapoint: 0.0004862995382535963




Fitting train time augmentor: [---------------------------------->     ] 88 %

Fitting train time augmentor: [--------------------------------------->] 100 %

Fit process completed after 14.136265516281128 seconds. Total datapoints fitted: 41123.
Average time per datapoint: 0.00034375569672157014




Fitting validation time augmentor: [--------------------------------------->] 100 %

Fit process completed after 1.6114263534545898 seconds. Total datapoints fitted: 3347.
Average time per datapoint: 0.00048145394486244096




Fitting test time augmentor: [--------------------------------------->] 100 %

Fit process completed after 1.1173195838928223 seconds. Total datapoints fitted: 2231.
Average time per datapoint: 0.0005008155911666617




Stage one loading training set, timeAug: [--------------------------------------->] 100 %

Stage one loading validation set, timeAug: [--------------------------------------->] 100 %

Stage one loading test set, timeAug: [--------------------------------------->] 100 %

Fit process of normalizer skipped as unecessary


Stage one loading noise set, timeAug: [--------------------------------------->] 100 %

Stage two loading noise set, labels and normalize scaler: [--------------------------------------->] 100 %

Fitting noise augmentor: [--------------------------------------->] 100 %



Stage two loading training set, labels and normalize scaler: [--------------------------------------->] 100 %

Stage two loading validation set, labels and normalize scaler: [--------------------------------------->] 100 %

Stage two loading test set, labels and normalize scaler: [--------------------------------------->] 100 %



Completed loading to RAM
Time elapsed to completion of load_to_ram_earth_

In [4]:
use_tensorboard = True
use_liveplots = False
use_custom_callback = True
use_early_stopping = True
start_from_scratch = False
use_reduced_lr = True
log_data = True

beta = 2

def clear_tensorboard_dir():
        import os
        import shutil
        path = f"{base_dir}/Tensorboard_dir/fit"
        files = os.listdir(path)
        print(files)
        for f in files:
            shutil.rmtree(os.path.join(path,f))
if use_tensorboard:
    clear_tensorboard_dir()


modelTrain = TrainSingleModelRam(noiseAug, helper,
                              loadData, model_type, num_channels, use_tensorboard, use_liveplots,
                              use_custom_callback, use_early_stopping, use_reduced_lr, ramLoader,
                              log_data = log_data, 
                              start_from_scratch = start_from_scratch, beta = beta)
params = {    
    "batch_size" : 128,
    "epochs" : 50,
    "learning_rate" : 0.001,
    "optimizer" : "rmsprop",
    "use_residuals" : False,
    "use_bottleneck" : True,
    "num_modules" : 4,
    "filter_size" : 88,
    "bottleneck_size" : 40,
    "num_filters" : 40,
    "residual_activation" : "relu",
    "module_activation" : "linear",
    "module_output_activation" : "relu",
    "output_layer_activation": "sigmoid",
    "reg_residual": False,
    "reg_module" : False,
    "l1_r" : 0,
    "l2_r" : 0
}
model = modelTrain.run(x_train, y_train, x_val, y_val, x_test, y_test, 16, 15, evaluate_train = True, evaluate_val = True, evaluate_test = True, meier_mode = False, **params)

['20210502-122759']
Trying to create result file
Made result file:  results_InceptionTime_earthExplo_timeAug_normalize_noiseAug_earlyS_unbalanced_valtest_subsample-0.25_numChannels-3_f2.csv
[   {'model_type': 'InceptionTime'},
    {   'batch_size': 128,
        'bottleneck_size': 40,
        'epochs': 50,
        'filter_size': 88,
        'l1_r': 0,
        'l2_r': 0,
        'learning_rate': 0.001,
        'module_activation': 'linear',
        'module_output_activation': 'relu',
        'num_filters': 40,
        'num_modules': 4,
        'optimizer': 'rmsprop',
        'output_layer_activation': 'sigmoid',
        'reg_module': False,
        'reg_residual': False,
        'residual_activation': 'relu',
        'use_bottleneck': True,
        'use_residuals': False}]
Saving file. 3 rows.
results_InceptionTime_earthExplo_timeAug_normalize_noiseAug_earlyS_unbalanced_valtest_subsample-0.25_numChannels-3_f2.csv saved to path:   /media/tord/T7/Thesis_ssd/MasterThesis3/GridSearchResults/

Epoch 1/50
26/26 [==============================] - 3s 91ms/step - loss: 0.8558 - precision: 0.0763 - recall: 1.0000 - binary_accuracy: 0.0763


KeyboardInterrupt: 

In [ ]:
conf, report, accuracy, precision, recall, fscore = helper.evaluate_generator(model, x_val, y_val, params["batch_size"],
                                                                             loadData.label_dict, num_channels, noiseAug,
                                                                             scaler_name, 2, plot_conf_matrix = True, plot_p_r_curve = True, beta = beta)

In [ ]:
accuracy, precision, recall, fscore

In [ ]:
save_dir = '/media/tord/T7/Thesis_ssd/SavedModels/InceptionTime'
model_name = 'IncpetionTime_EE_final'
model_path = f'{save_dir}/{model_name}'

model.save(model_path)
#model = tf.keras.models.load_model(model_path)

# 